# BranchPro: inference of R_t with negative binomial noise depending on overdispersion and number of observations

The notebook includes a figure displaying the posterior distribution used for the inference of the R_t profile and a figure of the inferred reproduction number profile for an example branching process model with negative binomial noise and different numbers of observations and values of the overdispersion parameters.

The reproduction number profile is assumed to be a constant function with R_t=1, $\forall$ t. The posterior distribution is plotted as a histogram. The mean and 95% interval quantiles are plotted together to illustrate a sensible trajectory of the R profile in time for inference.

In [1]:
# Import libraries
import numpy as np
import math
import itertools
import branchpro
import scipy.stats
import pints
import pints.plot
from matplotlib import pyplot as plt
from branchpro.apps import ReproductionNumberPlot
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
import pandas as pd

# Range of number of days for incidence data
num_timepoints_range = [10, 30, 50, 100]

# Range overdispersion parameter
phi_range = [0.002, 0.05, 0.5, 1.2]

# Number of reruns of the model incidence
num_runs = 10

## Parameterize example branching process model

In [2]:
# Build the serial interval w_s
ws_mean = 2.6
ws_var = 1.5**2
theta = ws_var / ws_mean
k = ws_mean / theta
w_dist = scipy.stats.gamma(k, scale=theta)

# Prior inference parameters using the NegBinBranchProPosterior
epsilon = 1
tau = 6
R_t_start = tau+1
a = 1
b = 1/5

logprior_phi = pints.UniformLogPrior(0, 5)

# Run inference for all simulated incidence for all choices of
# overdispersion and number of observations
all_extended_samples_old = []
all_ground_truth = []
all_new_intervals = []

for n, num_timepoints in enumerate(num_timepoints_range):
    nt_extended_samples_old = []
    nt_new_intervals = []

    # Set true R_t profile
    L = len(np.arange(R_t_start, num_timepoints))

    ground_truth = pd.DataFrame({
        'Time Points': np.arange(R_t_start, num_timepoints),
        'R_t': L*[1]
    })

    for p, phi in enumerate(phi_range):
        reruns_extended_samples_old = []
        reruns_new_intervals = []
        for _ in range(num_runs):
            # Build the serial interval w_s
            disc_w = w_dist.pdf(np.arange(num_timepoints))

            # Construct NegBinBranchProModel object
            initial_r = 3
            serial_interval = disc_w
            m = branchpro.NegBinBranchProModel(initial_r, serial_interval, phi)

            new_rs = [1]          # sequence of R_0 numbers
            start_times = [0]      # days at which each R_0 period begins
            m.set_r_profile(new_rs, start_times)
            parameters = 100 # initial number of cases
            times = np.arange(num_timepoints)

            cases = m.simulate(parameters, times)

            # Transform our incidence data into pandas dataframes
            inc_data = pd.DataFrame(
                {
                    'Time': np.arange(num_timepoints),
                    'Incidence Number': cases
                }
            )

            inference_new = branchpro.NegBinBranchProLogPosterior(
                inc_data=inc_data,
                daily_serial_interval=serial_interval,
                tau=tau,
                phi=phi,
                alpha=a,
                beta=1/b,
                infer_phi=True,
                phi_prior=logprior_phi)

            samples = inference_new.run_inference(num_iter=100)

            # Plot histograms of the parameters inferred for South West
            param_names = []

            if inference_new._infer_phi is True:
                for _ in range(inference_new.lprior.n_parameters()-1):
                    param_names.append('R_t{}'.format(_ + R_t_start))
                param_names.append('Phi')

                # Eliminate burn-in iterations (1/2 of the chain lengths)
                samples_old = samples.copy()
                samples = samples[:, 50:, :-1]

            else:
                for _ in range(inference_new.lprior.n_parameters()):
                    param_names.append('R_t{}'.format(_ + R_t_start))

                # Eliminate burn-in iterations (1/2 of the chain lengths)
                samples_old = samples.copy()
                samples = samples[:, 50:, :]

            # Evaluate the model for all parameter sets in the samples
            n_chains, n_sample, n_param = samples.shape

            extended_samples_old = np.concatenate((samples_old[:, 50:, :][0], samples_old[:, 50:, :][1], samples_old[:, 50:, :][2]), axis=0)
            extended_samples = np.concatenate((samples[0], samples[1], samples[2]), axis=0)

            thinning = max(1, int(n_sample * n_chains / 50))

            new_intervals = pd.DataFrame({
                'Time Points': np.arange(R_t_start, num_timepoints),
                'Mean': np.mean(extended_samples[::thinning, :], axis=0),
                'Lower bound CI': np.quantile(extended_samples[::thinning, :], 0.025, axis=0),
                'Upper bound CI': np.quantile(extended_samples[::thinning, :], 0.975, axis=0),
                'Central Probability': L * [0.95]
            })

            reruns_extended_samples_old.append(extended_samples_old)
            reruns_new_intervals.append(new_intervals)

        nt_extended_samples_old.append(reruns_extended_samples_old)
        nt_new_intervals.append(reruns_new_intervals)

    all_extended_samples_old.append(nt_extended_samples_old)
    all_ground_truth.append(ground_truth)
    all_new_intervals.append(nt_new_intervals)

/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1018: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.1 *
/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1021: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.2 *


Running...
Using No-U-Turn MCMC
Generating 3 chains.
Running in sequential mode.
Iter. Eval. Accept.   Steps. Accept.   Steps. Accept.   Steps. Time m:s
0     24     0.25     1       0.17     1       0.25     1        0:00.0
1     27     0.25     1       0.25     1       0.25     1        0:00.0
2     30     0.25     1       0.25     1       0.25     1        0:00.0
3     33     0.25     1       0.5      1       0.25     1        0:00.0
20    768    0.739    14      0.752    8       0.745    9        0:00.5
40    1380   0.727    10      0.747    13      0.751    15       0:00.9
60    2346   0.774    10      0.736    19      0.734    20       0:01.5
80    3096   0.761    11      0.756079 17      0.752    12       0:02.0
100   3527   0.492    10      0.744    14      0.753    8        0:02.2
Halting: Maximum number of iterations (100) reached.
Done!
param    mean    std.    2.5%    25%    50%    75%    97.5%    rhat    ess    ess per sec.
-------  ------  ------  ------  -----  -----  --

/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1018: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.1 *
/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1021: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.2 *


20    498    0.746    8       0.739    7       0.762    9        0:00.3
40    1032   0.752    6       0.761    11      0.748    9        0:00.7
60    1542   0.779    8       0.756    7       0.73542  9        0:01.0
80    2106   0.715    11      0.76     8       0.774    9        0:01.3
100   2404   0.723    11      0.6586   7       0.733    8        0:01.5
Halting: Maximum number of iterations (100) reached.
Done!
param    mean    std.    2.5%    25%    50%    75%    97.5%    rhat    ess    ess per sec.
-------  ------  ------  ------  -----  -----  -----  -------  ------  -----  --------------
R_t7     0.84    0.15    0.44    0.80   0.86   0.90   1.07     1.02    51.33  33.46
R_t8     0.91    0.16    0.44    0.85   0.91   1.00   1.15     1.00    63.90  41.65
R_t9     0.94    0.15    0.53    0.90   0.96   1.01   1.15     1.01    55.81  36.38
Phi      0.15    0.46    0.00    0.02   0.04   0.07   1.89     1.03    41.29  26.91
Running...
Using No-U-Turn MCMC
Generating 3 chains.
Running 

/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1018: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.1 *
/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1021: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.2 *


...

Iter. Eval. Accept.   Steps. Accept.   Steps. Accept.   Steps. Time m:s
0     87     0.427    2       0.476    2       0.282    13       0:01.1
1     90                                       0.25     1        0:01.2
2     93                                       0.25     1        0:01.2
3     186    0.5      16      0.5      16      0.473    16       0:02.4
20    2973   0.754    56      0.733    46      0.741    52       0:37.1
40    6735   0.755    60      0.761    63      0.770203 52       1:23.6
60    10044  0.758    48      0.778    63      0.729    55       2:04.5
80    13164  0.752    53      0.757    47      0.757709 57       2:44.3
100   15726  0.762    45      0.742    48      0.769    42       3:16.5
Halting: Maximum number of iterations (100) reached.
Done!
param    mean    std.    2.5%    25%    50%    75%    97.5%    rhat    ess     ess per sec.
-------  ------  ------  ------  -----  -----  -----  -------  ------  ------  --------------
R_t7     0.54    0.18    0.22    0.

/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1018: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.1 *
/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1021: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.2 *


Iter. Eval. Accept.   Steps. Accept.   Steps. Accept.   Steps. Time m:s
0     18     0.25     1       0.25     1       0.25     1        0:00.2
1     21     0.25     1       0.25     1       0.25     1        0:00.3
2     24     0.25     1       0.25     1       0.25     1        0:00.3
3     27     0.25     1       0.25     1       0.25     1        0:00.4
20    1275   0.735    21      0.73966  24      0.773    21       0:15.8
40    2682   0.765    25      0.779    21      0.738    22       0:33.2
60    3720   0.774    17      0.748    19      0.759841 16       0:46.1
80    4836   0.745    18      0.758    18      0.755851 16       1:00.1
100   5687   0.751    18      0.744    16      0.723    15       1:10.7
Halting: Maximum number of iterations (100) reached.
Done!
param    mean    std.    2.5%    25%    50%    75%    97.5%    rhat    ess     ess per sec.
-------  ------  ------  ------  -----  -----  -----  -------  ------  ------  --------------
R_t7     0.45    0.19    0.20    0.

/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1018: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.1 *
/Users/ioaros/Desktop/Software Project/branchpro/branchpro/new_posterior.py:1021: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  (np.array(self.lprior.mean()) + 0.2 *


Iter. Eval. Accept.   Steps. Accept.   Steps. Accept.   Steps. Time m:s
0     12     0.25     1       0.25     1       0.25     1        0:00.2
1     15     0.25     1       0.25     1       0.25     1        0:00.2
2     18     0.25     1       0.25     1       0.25     1        0:00.2
3     27     0.25     1       0.25     1       0.375    2        0:00.4
20    1596   0.752555 26      0.786    12      0.764365 30       0:19.9
40    3186   0.773    29      0.764    23      0.758524 24       0:39.8
60    4596   0.768    23      0.768    19      0.746    22       0:57.6
80    5660   0.759    24      0.674941 14      0.764    25       1:10.9
100   6397   0.742    19                       0.765769 20       1:20.1
Halting: Maximum number of iterations (100) reached.
Done!
param    mean    std.    2.5%    25%    50%    75%    97.5%    rhat    ess    ess per sec.
-------  ------  ------  ------  -----  -----  -----  -------  ------  -----  --------------
R_t7     1.04    0.46    0.21    0.87

## Posterior Distribution of Rt

In [7]:
colours = ['red', 'blue']

list_titles = ['ϕ={}, N_t={}'.format(phi, num) for phi, num in list(
    itertools.product(phi_range, num_timepoints_range))]

fig = go.Figure()
fig = make_subplots(rows=len(phi_range), cols=len(num_timepoints_range), subplot_titles=tuple(list_titles))

for p, phi in enumerate(phi_range):
    for n, num_timepoints in enumerate(num_timepoints_range):
        hist_data = []
        group_labels = ['Incidence run {}'.format(_+1) for _ in range(num_runs)]
        for _ in range(num_runs):
            hist_data.append(all_extended_samples_old[n][p][_][::thinning, -1])
        
        fig2 = ff.create_distplot(hist_data, group_labels)

        for _ in range(num_runs):
            fig.add_trace(
                go.Scatter(
                    fig2['data'][num_runs+_],
                    line=dict(
                        color=colours[0]),
                    showlegend=False
                    ),
                    row=p+1,
                    col=n+1)

fig.update_layout(
    title='Posterior Distribution',
    width=800,
    height=800,
    xaxis13_title='ϕ',
    xaxis14_title='ϕ',
    xaxis15_title='ϕ',
    xaxis16_title='ϕ',
    yaxis_title='P(ϕ|x)',
    yaxis5_title='P(ϕ|x)',
    yaxis9_title='P(ϕ|x)',
    yaxis13_title='P(ϕ|x)')

fig.show()

## Inference plot of Rt trajectories

In [9]:
fig = go.Figure()
fig = make_subplots(rows=len(phi_range), cols=len(num_timepoints_range), subplot_titles=tuple(list_titles))

for p, phi in enumerate(phi_range):
    for n, num_timepoints in enumerate(num_timepoints_range):
        if (p != 0) or (n != 0):
            fig.add_trace(
                go.Scatter(
                    y=all_ground_truth[n]['R_t'],
                    x=all_ground_truth[n]['Time Points'],
                    mode='lines',
                    name='True R',
                    line_color=colours[0],
                    showlegend=False
                ),
                row=p+1, col=n+1
            )

            for _ in range(num_runs):
                fig.add_trace(
                    go.Scatter(
                        y=all_new_intervals[n][p][_]['Mean'],
                        x=all_new_intervals[n][p][_]['Time Points'],
                        mode='lines',
                        name='Estimated R',
                        line_color=colours[1],
                        showlegend=False
                    ),
                    row=p+1, col=n+1
                )

                fig.add_trace(
                    go.Scatter(
                        x=list(all_new_intervals[n][p][_]['Time Points']) + list(all_new_intervals[n][p][_]['Time Points'])[::-1],
                        y=list(all_new_intervals[n][p][_]['Upper bound CI']) + list(all_new_intervals[n][p][_]['Lower bound CI'])[::-1],
                        fill='toself',
                        fillcolor=colours[1],
                        line_color=colours[1],
                        opacity=0.5,
                        mode='lines',
                        name='Credible interval {:.8f}'.format(all_new_intervals[p][n][_]['Central Probability'][0]).rstrip('0'),
                        showlegend=False
                    ),
                    row=p+1, col=n+1
                )

        else:
            fig.add_trace(
                go.Scatter(
                    y=all_ground_truth[n]['R_t'],
                    x=all_ground_truth[n]['Time Points'],
                    mode='lines',
                    name='True R',
                    line_color=colours[0]
                ),
                row=p+1, col=n+1
            )

            for _ in range(num_runs):
                if _ != 0:
                    fig.add_trace(
                        go.Scatter(
                            y=all_new_intervals[n][p][_]['Mean'],
                            x=all_new_intervals[n][p][_]['Time Points'],
                            mode='lines',
                            name='Estimated R',
                            line_color=colours[1],
                            showlegend=False
                        ),
                        row=p+1, col=n+1
                    )

                    fig.add_trace(
                        go.Scatter(
                            x=list(all_new_intervals[n][p][_]['Time Points']) + list(all_new_intervals[n][p][_]['Time Points'])[::-1],
                            y=list(all_new_intervals[n][p][_]['Upper bound CI']) + list(all_new_intervals[n][p][_]['Lower bound CI'])[::-1],
                            fill='toself',
                            fillcolor=colours[1],
                            line_color=colours[1],
                            opacity=0.5,
                            mode='lines',
                            name='Credible interval {:.8f}'.format(all_new_intervals[p][n][_]['Central Probability'][0]).rstrip('0'),
                            showlegend=False
                        ),
                        row=p+1, col=n+1
                    )

                else:
                    fig.add_trace(
                        go.Scatter(
                            y=all_new_intervals[n][p][_]['Mean'],
                            x=all_new_intervals[n][p][_]['Time Points'],
                            mode='lines',
                            name='Estimated R',
                            line_color=colours[1]
                        ),
                        row=p+1, col=n+1
                    )

                    fig.add_trace(
                        go.Scatter(
                            x=list(all_new_intervals[n][p][_]['Time Points']) + list(all_new_intervals[n][p][_]['Time Points'])[::-1],
                            y=list(all_new_intervals[n][p][_]['Upper bound CI']) + list(all_new_intervals[n][p][_]['Lower bound CI'])[::-1],
                            fill='toself',
                            fillcolor=colours[1],
                            line_color=colours[1],
                            opacity=0.5,
                            mode='lines',
                            name='Credible interval {:.8f}'.format(all_new_intervals[p][n][_]['Central Probability'][0]).rstrip('0'),
                        ),
                        row=p+1, col=n+1
                    )

fig.update_layout(
    title='Reproduction Number',
    width=1800,
    height=1800,
    xaxis13_title='Time (Day)',
    xaxis14_title='Time (Day)',
    xaxis15_title='Time (Day)',
    xaxis16_title='Time (Day)',
    yaxis_title='R_t',
    yaxis5_title='R_t',
    yaxis9_title='R_t',
    yaxis13_title='R_t')

fig.show()

## Incidences plot

In [18]:
fig = go.Figure()
fig = make_subplots(rows=len(phi_range), cols=len(num_timepoints_range), subplot_titles=tuple(list_titles))

for n, num_timepoints in enumerate(num_timepoints_range):
    for p, phi in enumerate(phi_range):
        reruns_extended_samples_old = []
        reruns_new_intervals = []
        # Build the serial interval w_s
        disc_w = w_dist.pdf(np.arange(num_timepoints))

        # Construct NegBinBranchProModel object
        initial_r = 3
        serial_interval = disc_w
        m = branchpro.NegBinBranchProModel(initial_r, serial_interval, phi)

        new_rs = [1]          # sequence of R_0 numbers
        start_times = [0]      # days at which each R_0 period begins
        m.set_r_profile(new_rs, start_times)
        parameters = 100 # initial number of cases
        times = np.arange(num_timepoints)

        cases = m.simulate(parameters, times)

        # Transform our incidence data into pandas dataframes
        inc_data = pd.DataFrame(
            {
                'Time': np.arange(num_timepoints),
                'Incidence Number': cases
            }
        )

        # Plot of incidences
        fig.add_trace(
            go.Bar(
                x=times,
                y=cases,
                name='Incidences',
                marker_color=colours[1],
                showlegend=False
            ),
            row=p+1, col=n+1
        )

# Add axis labels
fig.update_layout(
    title='Incidences',
    width=800,
    height=800,
    xaxis13_title='Time (days)',
    xaxis14_title='Time (days)',
    xaxis15_title='Time (days)',
    xaxis16_title='Time (days)',
    yaxis_title='New cases',
    yaxis5_title='New cases',
    yaxis9_title='New cases',
    yaxis13_title='New cases'
)

fig.show()